Imports and other things to start the project

In [1]:
!pip install fastparquet

In [9]:
!pip install matplotlib

  Using cached contourpy-1.3.1-cp311-cp311-win_amd64.whl.metadata (5.4 kB)
  Using cached cycler-0.12.1-py3-none-any.whl.metadata (3.8 kB)
   ---------------------------------------- 0.0/8.1 MB ? eta -:--:--
   ----------------------------------- ---- 7.1/8.1 MB 36.4 MB/s eta 0:00:01
   ---------------------------------------- 8.1/8.1 MB 31.2 MB/s eta 0:00:00
Using cached contourpy-1.3.1-cp311-cp311-win_amd64.whl (219 kB)
Using cached cycler-0.12.1-py3-none-any.whl (8.3 kB)
   ---------------------------------------- 0.0/2.2 MB ? eta -:--:--
   ---------------------------------------- 2.2/2.2 MB 41.3 MB/s eta 0:00:00


In [2]:
import pandas as pd
import re
import psutil
import json
import urllib.request
import fastparquet
import os
import glob

In order to properly use this data, we must start by importing it and then preprocessing

In [3]:
file_path = "train-00000-of-00206.parquet"

df = pd.read_parquet(file_path, engine = "fastparquet")

first_entry_code = df.iloc[0]["content"]
second_entry_code = df.iloc[100]["content"]
third_entry_code = df.iloc[1000]["content"]

print(df)
print(first_entry_code)
print(second_entry_code)
print(third_entry_code)

                                          hexsha   size ext    lang  \
0       f70001f658d4dfaa72dd4f0d1b3176492f6658bb   6442  py  Python   
1       f7000273e22d5a0f2d5b40c38a0ed8511d1b8995   2250  py  Python   
2       f70002926d1d600b4b068459c9dd40ebf3aef47d    757  py  Python   
3       f7000327daf9ff11a381ce6d5de401ff007d1323   1094  py  Python   
4       f7000371f0315cd55c0b14b33e7e8e56697cfc2e  10498  py  Python   
...                                          ...    ...  ..     ...   
117540  793e7c8154dde86884b9669622b32aeea1185d21   1853  py  Python   
117541  793e7d1ab6c0471710bdbffc3c1b2a68e0aa3516    948  py  Python   
117542  793e7e0a68202e76b818772ff6d01655ca87546e   2485  py  Python   
117543  793e7ea61a6d183a0434da1b893d3870cec79aba   1406  py  Python   
117544  793e7fc5c6f5a39a1fb0909ab5a3e5ce33f87ab8  25955  py  Python   

                                      max_stars_repo_path  \
0                                       spider/openwrt.py   
1                        

In [4]:
# Get only the code

code_series = df["content"].head(1000)

code_series2 = df["content"].iloc[1000:2000]
print(code_series[1])

# UCF Senior Design 2017-18
# Group 38

from PIL import Image
import cv2
import imagehash
import math
import numpy as np

DIFF_THRES = 20
LIMIT = 2
RESIZE = 1000


def calc_hash(img):
    """
    Calculate the wavelet hash of the image
        img: (ndarray) image file
    """
    # resize image if height > 1000
    img = resize(img)
    return imagehash.whash(Image.fromarray(img))


def compare(hash1, hash2):
    """
    Calculate the difference between two images
        hash1: (array) first wavelet hash
        hash2: (array) second wavelet hash
    """
    return hash1 - hash2


def limit(img, std_hash, count):
    """
    Determine whether image should be removed from image dictionary in main.py
        img: (ndarray) image file
        std_hash: (array) wavelet hash of comparison standard
        count: (int) global count of images similar to comparison standard
    """
    # calculate hash for given image
    cmp_hash = calc_hash(img)

    # compare to standard
    diff = compar

In [6]:
# Preprocess

def clean_code(code):
    # Remove multiline docstrings 
    code = re.sub(r'"""[\s\S]*?"""', '', code)
    code = re.sub(r"'''[\s\S]*?'''", '', code)

    # Remove single-line comments 
    code = re.sub(r'#.*', '', code)

    # Remove blank lines
    code = re.sub(r'^\s*\n', '', code)

    return code

In [7]:
cleaned_data = code_series.apply(clean_code)

cleaned_data2 = code_series2.apply(clean_code)

print(cleaned_data[1])

from PIL import Image
import cv2
import imagehash
import math
import numpy as np

DIFF_THRES = 20
LIMIT = 2
RESIZE = 1000


def calc_hash(img):
    
    
    img = resize(img)
    return imagehash.whash(Image.fromarray(img))


def compare(hash1, hash2):
    
    return hash1 - hash2


def limit(img, std_hash, count):
    
    
    cmp_hash = calc_hash(img)

    
    diff = compare(std_hash, cmp_hash)

    
    if diff <= DIFF_THRES:
        
        if count >= LIMIT:
            return 'remove'

    
    else:
        
        return 'update_std'

    
    return 'continue'


def resize(img):
    
    
    width = np.shape(img)[1]
    height = np.shape(img)[0]

    
    if width > RESIZE:
        
        scale = RESIZE / width
        resized_img = cv2.resize(
            img, (RESIZE, math.floor(height / scale)), cv2.INTER_AREA)
        
        return resized_img

    
    return img


def set_standard(images, filename):
    
    return filename, calc_hash(images[filename]), 0



In [8]:
#Save as json
cleaned_data_list = cleaned_data.tolist()

formatted_data = [{"code": item} for item in cleaned_data_list]

payload = json.dumps(formatted_data, ensure_ascii=False).encode("utf-8")

output_filename = "cleaned_data.json"

with open(output_filename, "w") as f:
    json.dump(formatted_data, f, indent=4)

print(f"Data saved to {output_filename}")

cleaned_data_list2 = cleaned_data2.tolist()

formatted_data2 = [{"code": item} for item in cleaned_data_list]

payload2 = json.dumps(formatted_data2, ensure_ascii=False).encode("utf-8")

output_filename = "cleaned_data2.json"

with open(output_filename, "w") as f:
    json.dump(formatted_data, f, indent=4)

print(f"Data saved to {output_filename}")


Data saved to cleaned_data.json
Data saved to cleaned_data2.json


Generate summaries for data

In [9]:
#Check ollama
import psutil

def check_if_running(process_name):
    running = False
    for proc in psutil.process_iter(["name"]):
        if process_name in proc.info["name"]:
            running = True
            break
    return running

ollama_running = check_if_running("ollama")

if not ollama_running:
    raise RuntimeError("Ollama not running. Launch ollama before proceeding.")
print("Ollama running:", check_if_running("ollama"))

Ollama running: True


In [10]:
import urllib.request

def query_model(
    prompt,
    model="qwen2.5-coder:7b",
    url="http://localhost:11434/api/chat"
):
    
    data = {
        "model": model,
        "messages": [
            {"role": "user", "content": prompt}
        ],
        "options": {     
            "seed": 123,
            "temperature": 0,
            "num_ctx": 2048
        }
    }


    payload = json.dumps(data).encode("utf-8")

    request = urllib.request.Request(
        url,
        data=payload,
        method="POST"
    )
    request.add_header("Content-Type", "application/json")

   
    response_data = ""
    with urllib.request.urlopen(request) as response:
        
        while True:
            line = response.readline().decode("utf-8")
            if not line:
                break
            response_json = json.loads(line)
            response_data += response_json["message"]["content"]

    return response_data


model = "qwen2.5-coder:7b"
result = query_model("What do Llamas eat?", model)
print(result)

Llamas primarily eat grasses and hay. They are herbivores and have a digestive system that allows them to digest cellulose, which is found in plant material. In the wild, llamas graze on grasses, leaves, and bark from trees and bushes. In captivity or when kept as pets, they are usually fed commercial llama pellets, supplemented with fresh grass and hay.


In [11]:
def add_summaries_to_json(input_json_filename, output_json_filename):
    with open(input_json_filename, "r") as infile:
        code_data = json.load(infile)
    
    if not isinstance(code_data, list):
        raise ValueError("Expected a list of dictionaries but got a different format.")
    
    
    id = 0
    for entry in code_data:
        if not isinstance(entry, dict) or "code" not in entry:
            raise ValueError(f"Invalid entry format: {entry}")
        
        prompt = f"Summarize the following Python code in one or two sentences. Do not include any code snippets in your response.:\n{entry['code']}"
        summary = query_model(prompt)
        entry["summary"] = summary
        print(f"ID: {id}")
        print(f"Entry: {entry}")
        print("Summary: " + summary)
        print()
        print()
        id = id + 1

   
    with open(output_json_filename, "w") as outfile:
        json.dump(code_data, outfile, indent=4)


In [12]:
# Proof of concept

testdf = df["content"].head(10)

cleaned_test = testdf.apply(clean_code)

cleaned_data_list_test = cleaned_test.tolist()

formatted_data_test = [{"code": item} for item in cleaned_data_list_test]

payload_test = json.dumps(formatted_data_test, ensure_ascii=False).encode("utf-8")

output_filename = "cleaned_data_test.json"

with open(output_filename, "w") as f:
    json.dump(formatted_data_test, f, indent=4)

print(f"Data saved to {output_filename}")

add_summaries_to_json("cleaned_data_test.json", "summarized_code_test.json")

print("Summaries added and saved to summarized_code_test.json")

Data saved to cleaned_data_test.json
ID: 0
Entry: {'code': 'from   _TFL.pyk           import pyk\n\nfrom   rsclib.HTML_Parse  import tag, Page_Tree\nfrom   rsclib.autosuper   import autosuper\nfrom   spider.common      import Interface, Inet4, Inet6, unroutable\nfrom   spider.common      import WLAN_Config\nfrom   spider.luci        import Version_Mixin\n\nclass Status (Page_Tree, Version_Mixin) :\n    url          = \'cgi-bin/luci/freifunk/status/status\'\n    retries      = 2\n    timeout      = 10\n    html_charset = \'utf-8\' \n\n    wl_names = dict \\\n        ( ssid    = \'ssid\'\n        , _bsiid  = \'bssid\'\n        , channel = \'channel\'\n        , mode    = \'mode\'\n        )\n\n    def parse (self) :\n        root  = self.tree.getroot ()\n        self.wlans  = []\n        self.routes = {}\n        for div in root.findall (".//%s" % tag ("div")) :\n            id = div.get (\'id\')\n            if id == \'cbi-wireless\' :\n                wlan_div = div\n            elif i

KeyboardInterrupt: 

In [11]:
# Batching summarization

def split_json_into_batches(input_json_filename, output_dir="batches", batch_size=10):

    os.makedirs(output_dir, exist_ok=True)
    
    with open(input_json_filename, "r") as infile:
        code_data = json.load(infile)
    
    if not isinstance(code_data, list):
        raise ValueError("Expected a list of dictionaries but got a different format.")
    
    batch_filenames = []
    for i in range(0, len(code_data), batch_size):
        batch_data = code_data[i:i+batch_size]
        batch_filename = f"{output_dir}/batch_{i//batch_size}.json"
        
        with open(batch_filename, "w") as batch_file:
            json.dump(batch_data, batch_file, indent=4)
        
        batch_filenames.append(batch_filename)
    
    print(f"Split {input_json_filename} into {len(batch_filenames)} batches in {output_dir}/")
    return batch_filenames

def process_batch_file(input_batch_filename, output_batch_filename=None):
    if output_batch_filename is None:
        base, ext = os.path.splitext(input_batch_filename)
        output_batch_filename = f"{base}_processed{ext}"
    
    with open(input_batch_filename, "r") as infile:
        batch_data = json.load(infile)
    
    for id, entry in enumerate(batch_data):
        if not isinstance(entry, dict) or "code" not in entry:
            raise ValueError(f"Invalid entry format: {entry}")
        
        prompt = f"Summarize the following Python code in one or two sentences. Do not include any code snippets in your response. Answer in a paragraph with no extra bullets or lists.:\n{entry['code']}"
        summary = query_model(prompt)
        entry["summary"] = summary
        print(f"Processing batch {os.path.basename(input_batch_filename)}, entry ID: {id}")
        print(f"Entry: {entry}")
        print("Summary: " + summary)
        print()
    
    with open(output_batch_filename, "w") as outfile:
        json.dump(batch_data, outfile, indent=4)
    
    print(f"Processed batch written to {output_batch_filename}")
    return output_batch_filename

def combine_processed_batches(processed_batch_pattern, output_json_filename):
    processed_files = sorted(glob.glob(processed_batch_pattern))
    
    if not processed_files:
        raise ValueError(f"No files found matching pattern: {processed_batch_pattern}")
    
    combined_data = []
    
    for filename in processed_files:
        with open(filename, "r") as f:
            batch_data = json.load(f)
            combined_data.extend(batch_data)
    
    with open(output_json_filename, "w") as outfile:
        json.dump(combined_data, outfile, indent=4)
    
    print(f"Combined {len(processed_files)} batches with {len(combined_data)} total entries")
    print(f"Output written to {output_json_filename}")
    
    return len(combined_data)

In [12]:
# Use batching for summarization

#batch_files = split_json_into_batches("cleaned_data.json", batch_size=10)

batch_files2 = split_json_into_batches("cleaned_data2.json", batch_size=10)

Split cleaned_data2.json into 100 batches in batches/


In [13]:
# Do the first 1000 entries
import time

batch_times = []

for i in range(100):
    if i < len(batch_files2):
        start_time = time.time()
        print(f"Processing batch {i}")
        process_batch_file(f"batches/batch_{i}.json")
        batch_time = time.time() - start_time
        print(f"Batch {i} took {batch_time}s to summarize")
        batch_times.append({"batch": i, "time": batch_time})
    else:
        print(f"Batch {i} does not exist - fewer than 10 batches total")

with open("batch_times2.json", "w") as f:
    json.dump(batch_times, f, indent=4)

Processing batch 0
Processing batch batch_0.json, entry ID: 0
Entry: {'code': 'from   _TFL.pyk           import pyk\n\nfrom   rsclib.HTML_Parse  import tag, Page_Tree\nfrom   rsclib.autosuper   import autosuper\nfrom   spider.common      import Interface, Inet4, Inet6, unroutable\nfrom   spider.common      import WLAN_Config\nfrom   spider.luci        import Version_Mixin\n\nclass Status (Page_Tree, Version_Mixin) :\n    url          = \'cgi-bin/luci/freifunk/status/status\'\n    retries      = 2\n    timeout      = 10\n    html_charset = \'utf-8\' \n\n    wl_names = dict \\\n        ( ssid    = \'ssid\'\n        , _bsiid  = \'bssid\'\n        , channel = \'channel\'\n        , mode    = \'mode\'\n        )\n\n    def parse (self) :\n        root  = self.tree.getroot ()\n        self.wlans  = []\n        self.routes = {}\n        for div in root.findall (".//%s" % tag ("div")) :\n            id = div.get (\'id\')\n            if id == \'cbi-wireless\' :\n                wlan_div = div\

In [14]:
# Combine files

print(glob.glob("batches/batch_*_processed.json"))

#combine_processed_batches("batches/batch_*_processed.json", "summarized_data.json")

combine_processed_batches("batches/batch_*_processed.json", "summarized_data2.json")

['batches\\batch_0_processed.json', 'batches\\batch_10_processed.json', 'batches\\batch_11_processed.json', 'batches\\batch_12_processed.json', 'batches\\batch_13_processed.json', 'batches\\batch_14_processed.json', 'batches\\batch_15_processed.json', 'batches\\batch_16_processed.json', 'batches\\batch_17_processed.json', 'batches\\batch_18_processed.json', 'batches\\batch_19_processed.json', 'batches\\batch_1_processed.json', 'batches\\batch_20_processed.json', 'batches\\batch_21_processed.json', 'batches\\batch_22_processed.json', 'batches\\batch_23_processed.json', 'batches\\batch_24_processed.json', 'batches\\batch_25_processed.json', 'batches\\batch_26_processed.json', 'batches\\batch_27_processed.json', 'batches\\batch_28_processed.json', 'batches\\batch_29_processed.json', 'batches\\batch_2_processed.json', 'batches\\batch_30_processed.json', 'batches\\batch_31_processed.json', 'batches\\batch_32_processed.json', 'batches\\batch_33_processed.json', 'batches\\batch_34_processed.j

1000

In [15]:
combine_processed_batches("summarized_data*.json", "full_summarized_data.json")

Combined 2 batches with 2000 total entries
Output written to full_summarized_data.json


2000

In [ ]:
combine_processed_batches("batches/batch_*_processed.json", "summarized_data2.json")

In [29]:
dfshort = df[['content']].copy()  # Keep it as a DataFrame, not a Series

# Apply cleaning function
dfshort['cleaned_content'] = dfshort['content'].apply(clean_code)

# Estimate token count
dfshort['token_estimate'] = dfshort['cleaned_content'].apply(lambda x: int(len(x.split()) * 1))

# Filter valid entries (≤ 1024 estimated tokens)
valid_entries = dfshort[dfshort['token_estimate'] <= 1000]

# Select the first 1000 valid entries
filtered_df = valid_entries.head(1000)[['cleaned_content']]

# Rename column for clarity
filtered_df.rename(columns={'cleaned_content': 'code'}, inplace=True)

# Save as JSON
filtered_df.to_json("filtered_entries.json", orient="records", indent=4)

print("Filtered entries saved as 'filtered_entries.json'")

Filtered entries saved as 'filtered_entries.json'


In [31]:
batch_filesshorter = split_json_into_batches("filtered_entries.json", batch_size=10)

Split filtered_entries.json into 100 batches in batches/


In [34]:
batch_times = []

for i in range(75, 100):
    if i < len(batch_filesshorter):
        start_time = time.time()
        print(f"Processing batch {i}")
        process_batch_file(f"batches/batch_{i}.json")
        batch_time = time.time() - start_time
        print(f"Batch {i} took {batch_time}s to summarize")
        batch_times.append({"batch": i, "time": batch_time})
    else:
        print(f"Batch {i} does not exist - fewer than 10 batches total")

with open("batch_times_shorter.json", "w") as f:
    json.dump(batch_times, f, indent=4)

Processing batch 75
Processing batch batch_75.json, entry ID: 0
Entry: {'code': 'import glob\nimport cv2\nimport os\n\n\ndef extract_frame(movie_files_dir, out_dir):\n    movie_files = glob.glob(movie_files_dir)\n\n    if not movie_files:\n        print(\'movie files are not found.\')\n        return\n\n    for movie_file in movie_files:\n        ext = movie_file.split(\'.\')[-1]\n        if not ext == \'mp4\' or not ext == \'MP4\':\n            print(f"can\'t extract this movie file: {movie_file}")\n            continue\n\n        out_dir = out_dir\n        if not os.path.exists(out_dir):\n            os.mkdir(out_dir)\n\n        cap = cv2.VideoCapture(movie_file)\n        if not cap.isOpened():\n            print(f"can\'t extract this movie file: {movie_file}")\n            return\n\n        digit = len(str(int(cap.get(cv2.CAP_PROP_FRAME_COUNT))))\n        n = 0\n        while True:\n            ret, frame = cap.read()\n            if ret:\n                cv2.imwrite(f"{movie_file}_

In [35]:
combine_processed_batches("batches/batch_*_processed.json", "summarized_data_shorter.json")

Combined 99 batches with 990 total entries
Output written to summarized_data_shorter.json


990